In [1]:
import json
import codecs

In [2]:
import pandas as pd
import os

### Seleccion del corpus SQuAD

In [4]:
SQUAD_TRAIN = 'squad/train-v2.0.json'
SQUAD_DEV = 'squad/dev-v2.0.json'

In [114]:
DATASET = SQUAD_TRAIN #SQUAD_TRAIN #SQUAD_DEV
FILE_XLSX = 'SQUAD-train_queries.xlsx' #'SQUAD-train_queries.xlsx' #'SQUAD-dev_queries.xlsx'

In [78]:
with codecs.open(DATASET, 'r', encoding='utf-8') as f:
    squad_dataset = json.load(f)

In [65]:
#print(squad_dataset['data'][0].keys())
#print(squad_dataset['data'][0]['paragraphs'][0].keys())
#print(squad_dataset['data'][0]['paragraphs'])

In [63]:
#print(squad_dataset['data'][1]['title'])
#print(squad_dataset['data'][1]['paragraphs'][1]['qas'][1]['question'])
#print(squad_dataset['data'][1]['paragraphs'][1]['qas'][1]['answers'])
#print(squad_dataset['data'][1]['paragraphs'][1]['context'])

In [79]:
titles_list = [paragraph_struct.get('title', 'None') for paragraph_struct in squad_dataset['data']]
print(len(titles_list))

35


In [80]:
paragraphs_list = [paragraph_struct['paragraphs'] for paragraph_struct in squad_dataset['data']]
# count paragraphs per article
count_paragraphs = [len(paragrahps_struct) for paragrahps_struct in paragraphs_list]
paragraphs_list = sum(paragraphs_list, [])
print(len(paragraphs_list))
print(sum(count_paragraphs))

1204
1204


In [81]:
qas_list = [qas_struct['qas'] for qas_struct in paragraphs_list]
# count queries per paragraph
count_queries_list = [len(qas_struct) for qas_struct in qas_list]
qas_list = sum(qas_list, [])
print(len(qas_list))
print(qas_list[0])
query_list = [qas_struct['question'] for qas_struct in qas_list]
answer_list = [qas_struct['answers'] for qas_struct in qas_list]
impossible_list = [qas_struct['is_impossible'] for qas_struct in qas_list]
ids_list = [qas_struct['id'] for qas_struct in qas_list]
plausible_list = [qas_struct.get('plausible_answers', '') for qas_struct in qas_list]
print(len(query_list))
print(len(answer_list))
print(query_list[0])
print(answer_list[0])

11873
{'question': 'In what country is Normandy located?', 'id': '56ddde6b9a695914005b9628', 'answers': [{'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}], 'is_impossible': False}
11873
11873
In what country is Normandy located?
[{'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}]


In [82]:
context_list = [qas_struct['context'] for qas_struct in paragraphs_list]
print(len(context_list))
print(context_list[0])

1204
The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.


In [83]:
context_freq_list = [[context_list[i]]*count_queries_list[i] for i in range(0,len(context_list))]
context_freq_list = sum(context_freq_list, [])
print(len(context_freq_list))
print(context_freq_list[0])

11873
The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.


In [84]:
title_freq_list = []
index_qas = 0
for struct_element in squad_dataset['data']:
    title = struct_element['title']
    num_paragraphs = len(struct_element['paragraphs'])
    num_qas = sum([len(element['qas']) for element in struct_element['paragraphs']])
    title_freq_list += [title]*num_qas
print(len(title_freq_list))

11873


In [86]:
dataset = ['dev']*len(query_list)
print(len(dataset))

11873


In [87]:
queries_pd = pd.DataFrame({ 'title': title_freq_list, 'id': ids_list, 'query': query_list, 'answer': answer_list, 'impossible': impossible_list,'plausible': plausible_list, 'dataset': dataset, 'context': context_freq_list})
queries_pd['answer'] = queries_pd['answer'].apply(lambda x: x[0]['text'] if len(x) > 0 else '')
queries_pd['plausible'] = queries_pd['plausible'].apply(lambda x: x[0]['text'] if len(x) > 0 else '')
queries_pd.tail()

title                        id  \
11868  Force  5737aafd1c456719005744ff   
11869  Force  5ad28ad0d7d075001a4299cc   
11870  Force  5ad28ad0d7d075001a4299cd   
11871  Force  5ad28ad0d7d075001a4299ce   
11872  Force  5ad28ad0d7d075001a4299cf   

                                                   query  answer  impossible  \
11868  What is the seldom used force unit equal to on...  sthène       False   
11869           What does not have a metric counterpart?                True   
11870  What is the force exerted by standard gravity ...                True   
11871  What force leads to a commonly used unit of mass?                True   
11872        What force is part of the modern SI system?                True   

            plausible dataset  \
11868                     dev   
11869     pound-force     dev   
11870  kilogram-force     dev   
11871  kilogram-force     dev   
11872  kilogram-force     dev   

                                                 context  
11868  The pound-force has a metric counterpart, less...  
11869  The pound-force has a metric counterpart, less...  
11870  The pound-force has a metric counterpart, less...  
11871  The pound-force has a metric counterpart, less...  
11872  The pound-force has a metric counterpart, less...

In [88]:
queries_pd.to_excel(FILE_XLSX, index=False)

In [115]:
queries_pd = pd.read_excel(FILE_XLSX)

In [116]:
queries_pd.head()

title                        id  \
0  Beyoncé  56be85543aeaaa14008c9063   
1  Beyoncé  56be85543aeaaa14008c9065   
2  Beyoncé  56be85543aeaaa14008c9066   
3  Beyoncé  56bf6b0f3aeaaa14008c9601   
4  Beyoncé  56bf6b0f3aeaaa14008c9602   

                                               query               answer  \
0           When did Beyonce start becoming popular?    in the late 1990s   
1  What areas did Beyonce compete in when she was...  singing and dancing   
2  When did Beyonce leave Destiny's Child and bec...                 2003   
3      In what city and state did Beyonce  grow up?        Houston, Texas   
4         In which decade did Beyonce become famous?           late 1990s   

   impossible plausible dataset  \
0       False       NaN   train   
1       False       NaN   train   
2       False       NaN   train   
3       False       NaN   train   
4       False       NaN   train   

                                             context  
0  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...  
1  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...  
2  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...  
3  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...  
4  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...

In [117]:
queries_pd = queries_pd.fillna('')

# PLN

In [9]:
import re
def preprocess_text(text_str):
    regular_expr = re.compile('\n|\r|\t|\(|\)|\[|\]|:|\,|\;|"|\?|\-|\%')
    text_str = re.sub(regular_expr, ' ', text_str)
    token_list = text_str.split(' ')
    token_list = [element for element in token_list if element]
    return ' '.join(token_list)

### POSTagging

In [16]:
# https://www.cis.uni-muenchen.de/~schmid/tools/TreeTagger/
import treetaggerwrapper

In [92]:
tagger = treetaggerwrapper.TreeTagger(TAGLANG='en', TAGDIR='C:\\Users\\larao_000\\Documents\\nlp\\tree-tagger-windows-3.2.3\\TreeTagger\\')

In [59]:
def pos_tagging(text, max_length=1000):
    results = []
    for i in range(0, len(text), max_length):
        partial_text = text[i:i+max_length]
        tags = tagger.tag_text(partial_text)
        results += treetaggerwrapper.make_tags(tags)
    return results

In [2]:
#print(queries_pd['context'][100])
#pos_tagging(queries_pd['context'][100])
#treetaggerwrapper.make_tags(tagger.tag_text(queries_pd['context'][100]))

In [118]:
queries_pd['query_pos'] = queries_pd['query'].apply(lambda x: treetaggerwrapper.make_tags(tagger.tag_text(x)))

In [119]:
queries_pd['answer_pos'] = queries_pd['answer'].apply(lambda x: treetaggerwrapper.make_tags(tagger.tag_text(x)))

In [120]:
queries_pd['plausible_pos'] = queries_pd['plausible'].apply(lambda x: treetaggerwrapper.make_tags(tagger.tag_text(x)))

In [121]:
queries_pd['context_pos'] = None
print(len(queries_pd['context_pos'].isna()))
for context in queries_pd['context'].unique():
    print(len(queries_pd.loc[queries_pd['context'] == context, 'context_pos']))
    ner_values = treetaggerwrapper.make_tags(tagger.tag_text(context))
    queries_pd.loc[queries_pd['context'] == context, 'context_pos'] = str(ner_values)
    print(sum(queries_pd['context_pos'].isna()))

130319
15
130304
12
130292
12
130280
13
130267
11
130256
13
130243
13
130230
10
130220
11
130209
15
130194
14
130180
10
130170
11
130159
13
130146
14
130132
13
130119
14
130105
11
130094
13
130081
13
130068
13
130055
12
130043
13
130030
10
130020
16
130004
8
129996
13
129983
12
129971
12
129959
10
129949
9
129940
12
129928
4
129924
13
129911
12
129899
13
129886
9
129877
12
129865
11
129854
8
129846
12
129834
12
129822
8
129814
10
129804
11
129793
13
129780
7
129773
8
129765
10
129755
10
129745
12
129733
12
129721
12
129709
15
129694
13
129681
12
129669
13
129656
10
129646
10
129636
9
129627
11
129616
11
129605
8
129597
9
129588
10
129578
12
129566
19
129547
17
129530
17
129513
11
129502
16
129486
11
129475
14
129461
14
129447
14
129433
15
129418
9
129409
14
129395
11
129384
14
129370
13
129357
13
129344
14
129330
7
129323
11
129312
10
129302
9
129293
13
129280
6
129274
11
129263
11
129252
10
129242
15
129227
9
129218
15
129203
9
129194
7
129187
13
129174
12
129162
8
129154
7
129147
7
1

124641
1
124640
2
124638
3
124635
3
124632
2
124630
2
124628
3
124625
1
124624
2
124622
1
124621
3
124618
3
124615
3
124612
2
124610
4
124606
3
124603
2
124601
5
124596
2
124594
5
124589
2
124587
3
124584
3
124581
3
124578
2
124576
2
124574
3
124571
2
124569
5
124564
2
124562
11
124551
12
124539
5
124534
5
124529
10
124519
6
124513
8
124505
10
124495
8
124487
2
124485
6
124479
3
124476
7
124469
7
124462
3
124459
6
124453
7
124446
5
124441
8
124433
8
124425
4
124421
5
124416
7
124409
6
124403
3
124400
7
124393
6
124387
10
124377
6
124371
9
124362
4
124358
7
124351
10
124341
7
124334
6
124328
8
124320
8
124312
4
124308
2
124306
8
124298
5
124293
8
124285
6
124279
4
124275
4
124271
10
124261
6
124255
5
124250
9
124241
8
124233
7
124226
7
124219
10
124209
4
124205
5
124200
7
124193
10
124183
8
124175
8
124167
6
124161
7
124154
8
124146
6
124140
4
124136
5
124131
9
124122
5
124117
8
124109
4
124105
7
124098
7
124091
6
124085
7
124078
5
124073
5
124068
5
124063
6
124057
8
124049
4
124045
9
1

7
119075
8
119067
6
119061
4
119057
5
119052
4
119048
6
119042
6
119036
3
119033
5
119028
4
119024
4
119020
2
119018
4
119014
4
119010
1
119009
4
119005
4
119001
4
118997
1
118996
2
118994
2
118992
1
118991
3
118988
2
118986
1
118985
1
118984
4
118980
3
118977
3
118974
3
118971
1
118970
3
118967
5
118962
4
118958
3
118955
2
118953
4
118949
3
118946
2
118944
2
118942
1
118941
4
118937
5
118932
1
118931
3
118928
1
118927
2
118925
2
118923
5
118918
2
118916
2
118914
1
118913
2
118911
1
118910
3
118907
2
118905
3
118902
1
118901
2
118899
3
118896
1
118895
2
118893
3
118890
2
118888
3
118885
4
118881
1
118880
3
118877
2
118875
2
118873
1
118872
3
118869
4
118865
4
118861
2
118859
3
118856
3
118853
4
118849
2
118847
3
118844
3
118841
1
118840
2
118838
1
118837
2
118835
1
118834
3
118831
3
118828
2
118826
1
118825
4
118821
3
118818
3
118815
5
118810
5
118805
5
118800
5
118795
3
118792
5
118787
5
118782
5
118777
5
118772
2
118770
5
118765
5
118760
4
118756
5
118751
2
118749
3
118746
5
118741
5

114445
4
114441
2
114439
4
114435
2
114433
3
114430
5
114425
3
114422
2
114420
2
114418
5
114413
1
114412
1
114411
1
114410
4
114406
1
114405
3
114402
4
114398
1
114397
1
114396
2
114394
2
114392
2
114390
3
114387
1
114386
3
114383
1
114382
2
114380
1
114379
2
114377
2
114375
1
114374
1
114373
3
114370
2
114368
2
114366
3
114363
1
114362
3
114359
4
114355
2
114353
1
114352
4
114348
4
114344
2
114342
2
114340
5
114335
1
114334
2
114332
3
114329
3
114326
2
114324
2
114322
1
114321
1
114320
1
114319
1
114318
9
114309
8
114301
9
114292
9
114283
9
114274
9
114265
9
114256
7
114249
9
114240
8
114232
9
114223
6
114217
8
114209
6
114203
10
114193
7
114186
6
114180
8
114172
6
114166
6
114160
10
114150
8
114142
9
114133
7
114126
9
114117
9
114108
10
114098
9
114089
7
114082
10
114072
8
114064
10
114054
8
114046
10
114036
9
114027
10
114017
10
114007
10
113997
10
113987
9
113978
10
113968
7
113961
9
113952
10
113942
10
113932
10
113922
7
113915
10
113905
10
113895
10
113885
5
113880
10
113870
8
1

8
108923
10
108913
10
108903
10
108893
9
108884
10
108874
8
108866
10
108856
8
108848
10
108838
9
108829
6
108823
8
108815
9
108806
9
108797
10
108787
6
108781
9
108772
10
108762
7
108755
10
108745
9
108736
8
108728
8
108720
8
108712
7
108705
8
108697
9
108688
10
108678
8
108670
1
108669
4
108665
2
108663
3
108660
5
108655
3
108652
4
108648
3
108645
3
108642
3
108639
5
108634
4
108630
4
108626
3
108623
1
108622
3
108619
5
108614
2
108612
2
108610
2
108608
4
108604
1
108603
3
108600
5
108595
2
108593
3
108590
2
108588
4
108584
3
108581
3
108578
2
108576
1
108575
2
108573
3
108570
5
108565
1
108564
3
108561
4
108557
3
108554
5
108549
4
108545
4
108541
2
108539
3
108536
5
108531
4
108527
3
108524
4
108520
1
108519
4
108515
3
108512
4
108508
3
108505
4
108501
4
108497
3
108494
3
108491
9
108482
8
108474
8
108466
8
108458
4
108454
4
108450
5
108445
5
108440
5
108435
4
108431
3
108428
5
108423
3
108420
5
108415
4
108411
3
108408
4
108404
4
108400
5
108395
5
108390
5
108385
5
108380
3
108377


...

33802
4
33798
5
33793
5
33788
5
33783
5
33778
5
33773
5
33768
5
33763
5
33758
8
33750
10
33740
9
33731
10
33721
10
33711
7
33704
7
33697
9
33688
10
33678
6
33672
9
33663
9
33654
10
33644
7
33637
10
33627
9
33618
8
33610
9
33601
6
33595
8
33587
8
33579
9
33570
9
33561
8
33553
9
33544
9
33535
8
33527
9
33518
9
33509
10
33499
9
33490
8
33482
10
33472
9
33463
9
33454
8
33446
9
33437
9
33428
9
33419
8
33411
10
33401
8
33393
8
33385
9
33376
9
33367
10
33357
9
33348
5
33343
5
33338
5
33333
5
33328
5
33323
5
33318
5
33313
5
33308
5
33303
5
33298
5
33293
5
33288
4
33284
5
33279
5
33274
4
33270
4
33266
5
33261
5
33256
5
33251
5
33246
5
33241
4
33237
5
33232
5
33227
4
33223
4
33219
4
33215
5
33210
4
33206
3
33203
5
33198
4
33194
5
33189
4
33185
5
33180
4
33176
4
33172
4
33168
4
33164
4
33160
5
33155
4
33151
5
33146
3
33143
5
33138
5
33133
5
33128
3
33125
4
33121
9
33112
9
33103
9
33094
9
33085
8
33077
9
33068
9
33059
9
33050
8
33042
8
33034
9
33025
8
33017
9
33008
8
33000
10
32990
8
32982
9
32973

26438
15
26423
9
26414
10
26404
10
26394
15
26379
15
26364
15
26349
15
26334
10
26324
9
26315
9
26306
9
26297
8
26289
9
26280
10
26270
9
26261
10
26251
10
26241
10
26231
10
26221
13
26208
15
26193
10
26183
13
26170
10
26160
10
26150
10
26140
10
26130
10
26120
10
26110
10
26100
10
26090
10
26080
10
26070
10
26060
10
26050
9
26041
10
26031
10
26021
10
26011
10
26001
10
25991
10
25981
10
25971
10
25961
10
25951
10
25941
10
25931
9
25922
10
25912
10
25902
10
25892
10
25882
10
25872
10
25862
10
25852
10
25842
10
25832
10
25822
10
25812
10
25802
11
25791
10
25781
10
25771
10
25761
10
25751
10
25741
10
25731
5
25726
5
25721
4
25717
5
25712
3
25709
4
25705
5
25700
5
25695
4
25691
4
25687
5
25682
5
25677
4
25673
5
25668
5
25663
5
25658
4
25654
4
25650
5
25645
5
25640
4
25636
5
25631
4
25627
3
25624
5
25619
5
25614
5
25609
3
25606
4
25602
5
25597
4
25593
4
25589
4
25585
4
25581
4
25577
4
25573
4
25569
4
25565
4
25561
5
25556
5
25551
5
25546
4
25542
4
25538
5
25533
5
25528
5
25523
5
25518
5
25513

19604
10
19594
9
19585
9
19576
9
19567
10
19557
10
19547
9
19538
9
19529
20
19509
20
19489
20
19469
20
19449
19
19430
19
19411
9
19402
10
19392
10
19382
8
19374
10
19364
10
19354
10
19344
10
19334
8
19326
10
19316
8
19308
8
19300
9
19291
8
19283
9
19274
9
19265
9
19256
9
19247
8
19239
9
19230
9
19221
8
19213
9
19204
10
19194
9
19185
10
19175
9
19166
10
19156
8
19148
9
19139
7
19132
9
19123
8
19115
10
19105
8
19097
8
19089
8
19081
10
19071
15
19056
15
19041
15
19026
13
19013
15
18998
14
18984
13
18971
14
18957
15
18942
14
18928
14
18914
14
18900
12
18888
14
18874
12
18862
14
18848
11
18837
15
18822
13
18809
14
18795
15
18780
12
18768
11
18757
15
18742
15
18727
11
18716
14
18702
15
18687
15
18672
12
18660
12
18648
14
18634
14
18620
13
18607
15
18592
13
18579
15
18564
15
18549
15
18534
14
18520
5
18515
5
18510
5
18505
4
18501
4
18497
4
18493
5
18488
5
18483
5
18478
5
18473
5
18468
5
18463
5
18458
5
18453
5
18448
5
18443
5
18438
5
18433
5
18428
5
18423
4
18419
5
18414
5
18409
5
18404
5
183

5
11572
5
11567
5
11562
5
11557
5
11552
4
11548
4
11544
3
11541
4
11537
4
11533
4
11529
10
11519
10
11509
10
11499
10
11489
10
11479
10
11469
10
11459
4
11455
10
11445
8
11437
10
11427
8
11419
8
11411
10
11401
8
11393
8
11385
10
11375
8
11367
10
11357
6
11351
9
11342
9
11333
10
11323
9
11314
9
11305
8
11297
8
11289
10
11279
9
11270
10
11260
10
11250
9
11241
9
11232
10
11222
9
11213
9
11204
9
11195
8
11187
8
11179
10
11169
8
11161
8
11153
9
11144
9
11135
9
11126
9
11117
9
11108
8
11100
8
11092
10
11082
10
11072
9
11063
9
11054
10
11044
10
11034
8
11026
9
11017
9
11008
9
10999
8
10991
8
10983
9
10974
9
10965
9
10956
5
10951
3
10948
3
10945
3
10942
5
10937
3
10934
3
10931
3
10928
3
10925
4
10921
4
10917
4
10913
4
10909
4
10905
4
10901
3
10898
4
10894
3
10891
5
10886
5
10881
5
10876
4
10872
4
10868
4
10864
5
10859
4
10855
3
10852
4
10848
4
10844
5
10839
3
10836
3
10833
4
10829
4
10825
5
10820
4
10816
3
10813
3
10810
4
10806
3
10803
3
10800
5
10795
4
10791
4
10787
4
10783
4
10779
5
10774
3


4714
5
4709
5
4704
5
4699
5
4694
5
4689
5
4684
5
4679
5
4674
5
4669
4
4665
3
4662
4
4658
3
4655
4
4651
3
4648
5
4643
3
4640
4
4636
5
4631
4
4627
4
4623
3
4620
4
4616
4
4612
3
4609
5
4604
5
4599
4
4595
4
4591
2
4589
5
4584
5
4579
5
4574
5
4569
4
4565
3
4562
5
4557
5
4552
4
4548
5
4543
4
4539
5
4534
4
4530
4
4526
4
4522
5
4517
4
4513
5
4508
5
4503
4
4499
3
4496
4
4492
3
4489
3
4486
4
4482
5
4477
5
4472
3
4469
5
4464
4
4460
4
4456
3
4453
4
4449
5
4444
4
4440
5
4435
3
4432
3
4429
5
4424
2
4422
5
4417
5
4412
3
4409
5
4404
5
4399
4
4395
4
4391
5
4386
4
4382
4
4378
5
4373
5
4368
10
4358
10
4348
8
4340
9
4331
9
4322
8
4314
7
4307
7
4300
9
4291
9
4282
8
4274
7
4267
8
4259
8
4251
9
4242
9
4233
8
4225
9
4216
8
4208
9
4199
9
4190
8
4182
9
4173
9
4164
9
4155
9
4146
8
4138
9
4129
9
4120
8
4112
19
4093
9
4084
10
4074
10
4064
10
4054
10
4044
10
4034
10
4024
10
4014
10
4004
10
3994
10
3984
9
3975
9
3966
10
3956
9
3947
9
3938
9
3929
10
3919
9
3910
10
3900
10
3890
9
3881
9
3872
9
3863
8
3855
9
3846
10
38

In [122]:
queries_pd.head()

title                        id  \
0  Beyoncé  56be85543aeaaa14008c9063   
1  Beyoncé  56be85543aeaaa14008c9065   
2  Beyoncé  56be85543aeaaa14008c9066   
3  Beyoncé  56bf6b0f3aeaaa14008c9601   
4  Beyoncé  56bf6b0f3aeaaa14008c9602   

                                               query               answer  \
0           When did Beyonce start becoming popular?    in the late 1990s   
1  What areas did Beyonce compete in when she was...  singing and dancing   
2  When did Beyonce leave Destiny's Child and bec...                 2003   
3      In what city and state did Beyonce  grow up?        Houston, Texas   
4         In which decade did Beyonce become famous?           late 1990s   

   impossible plausible dataset  \
0       False             train   
1       False             train   
2       False             train   
3       False             train   
4       False             train   

                                             context  \
0  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
1  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
2  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
3  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
4  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   

                                           query_pos  \
0  [(When, WRB, when), (did, VVD, do), (Beyonce, ...   
1  [(What, WP, what), (areas, NNS, area), (did, V...   
2  [(When, WRB, when), (did, VVD, do), (Beyonce, ...   
3  [(In, IN, in), (what, WP, what), (city, NN, ci...   
4  [(In, IN, in), (which, WDT, which), (decade, N...   

                                          answer_pos plausible_pos  \
0  [(in, IN, in), (the, DT, the), (late, JJ, late...            []   
1  [(singing, NN, singing), (and, CC, and), (danc...            []   
2                               [(2003, LS, @card@)]            []   
3  [(Houston, NP, Houston), (,, ,, ,), (Texas, NP...            []   
4            [(late, JJ, late), (1990s, NNS, 1990s)]            []   

                                         context_pos  
0  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...  
1  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...  
2  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...  
3  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...  
4  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...

In [123]:
informe_pd = queries_pd[['title', 'id', 'query', 'answer', 'impossible', 'plausible', 'dataset',
       'context', 'query_pos',  'answer_pos','plausible_pos', 'context_pos']] 

In [124]:
# 'POS-SQUAD-train-queries.xlsx'
informe_pd.to_excel('POS-SQUAD-train-queries.xlsx', index=False)

### NER Stanford

In [10]:
queries_pd = pd.read_excel('POS-SQUAD-train-queries.xlsx')

In [6]:
from stanfordcorenlp import StanfordCoreNLP

In [7]:
# https://www.khalidalnajjar.com/setup-use-stanford-corenlp-server-python/
# https://stanfordnlp.github.io/CoreNLP/index.html#download
# https://stanfordnlp.github.io/stanfordnlp/corenlp_client.html
nlp = StanfordCoreNLP('http://localhost', port=9000, timeout=30000)
props = {'annotators': 'tokenize,ssplit,pos,lemma,ner,parse,depparse,dcoref,relation',
          'pipelineLanguage': 'en',
          'outputFormat': 'json'
        }

In [8]:
def filter_ner_relevant(tuple_list):
    ner_dictionary = {}
    previous_ner = 'O'
    for element in tuple_list:
        if element[1] != 'O':
            if element[1] == previous_ner:
                ner_dictionary[element[1]][-1] += ' ' + element[0]
            elif element[1] in ner_dictionary.keys():
                ner_dictionary[element[1]].append(element[0])
            else:
                ner_dictionary[element[1]] = [element[0]]    
        previous_ner = element[1]
    return ner_dictionary

In [11]:
queries_pd['query_processed'] = queries_pd['query'].apply(preprocess_text)

In [12]:
queries_pd['query_ner'] = queries_pd['query_processed'].apply(nlp.ner)

In [13]:
#index = 4
#print(queries_pd['query_ner'].values[index])
#filter_ner_relevant(queries_pd['query_ner'].values[index])

In [14]:
queries_pd['query_ner'] = queries_pd['query_ner'].apply(filter_ner_relevant)

In [15]:
queries_pd['context_proc'] = queries_pd['context'].apply(preprocess_text)

In [16]:
queries_pd['context_ner'] = None
print(len(queries_pd['context_ner'].isna()))
for context in queries_pd['context_proc'].unique():
    print(len(queries_pd.loc[queries_pd['context_proc'] == context, 'context_ner']))
    ner_values = filter_ner_relevant(nlp.ner(context))
    queries_pd.loc[queries_pd['context_proc'] == context, 'context_ner'] = str(ner_values)
    print(sum(queries_pd['context_ner'].isna()))

130319
15
130304
12
130292
12
130280
13
130267
11
130256
13
130243
13
130230
10
130220
11
130209
15
130194
14
130180
10
130170
11
130159
13
130146
14
130132
13
130119
14
130105
11
130094
13
130081
13
130068
13
130055
12
130043
13
130030
10
130020
16
130004
8
129996
13
129983
12
129971
12
129959
10
129949
9
129940
12
129928
4
129924
13
129911
12
129899
13
129886
9
129877
12
129865
11
129854
8
129846
12
129834
12
129822
8
129814
10
129804
11
129793
13
129780
7
129773
8
129765
10
129755
10
129745
12
129733
12
129721
12
129709
15
129694
13
129681
12
129669
13
129656
10
129646
10
129636
9
129627
11
129616
11
129605
8
129597
9
129588
10
129578
12
129566
19
129547
17
129530
17
129513
11
129502
16
129486
11
129475
14
129461
14
129447
14
129433
15
129418
9
129409
14
129395
11
129384
14
129370
13
129357
13
129344
14
129330
7
129323
11
129312
10
129302
9
129293
13
129280
6
129274
11
129263
11
129252
10
129242
15
129227
9
129218
15
129203
9
129194
7
129187
13
129174
12
129162
8
129154
7
129147
7
1

124641
1
124640
2
124638
3
124635
3
124632
2
124630
2
124628
3
124625
1
124624
2
124622
1
124621
3
124618
3
124615
3
124612
2
124610
4
124606
3
124603
2
124601
5
124596
2
124594
5
124589
2
124587
3
124584
3
124581
3
124578
2
124576
2
124574
3
124571
2
124569
5
124564
2
124562
11
124551
12
124539
5
124534
5
124529
10
124519
6
124513
8
124505
10
124495
8
124487
2
124485
6
124479
3
124476
7
124469
7
124462
3
124459
6
124453
7
124446
5
124441
8
124433
8
124425
4
124421
5
124416
7
124409
6
124403
3
124400
7
124393
6
124387
10
124377
6
124371
9
124362
4
124358
7
124351
10
124341
7
124334
6
124328
8
124320
8
124312
4
124308
2
124306
8
124298
5
124293
8
124285
6
124279
4
124275
4
124271
10
124261
6
124255
5
124250
9
124241
8
124233
7
124226
7
124219
10
124209
4
124205
5
124200
7
124193
10
124183
8
124175
8
124167
6
124161
7
124154
8
124146
6
124140
4
124136
5
124131
9
124122
5
124117
8
124109
4
124105
7
124098
7
124091
6
124085
7
124078
5
124073
5
124068
5
124063
6
124057
8
124049
4
124045
9
1

119082
7
119075
8
119067
6
119061
4
119057
5
119052
4
119048
6
119042
6
119036
3
119033
5
119028
4
119024
4
119020
2
119018
4
119014
4
119010
1
119009
4
119005
4
119001
4
118997
1
118996
2
118994
2
118992
1
118991
3
118988
2
118986
1
118985
1
118984
4
118980
3
118977
3
118974
3
118971
1
118970
3
118967
5
118962
4
118958
3
118955
2
118953
4
118949
3
118946
2
118944
2
118942
1
118941
4
118937
5
118932
1
118931
3
118928
1
118927
2
118925
2
118923
5
118918
2
118916
2
118914
1
118913
2
118911
1
118910
3
118907
2
118905
3
118902
1
118901
2
118899
3
118896
1
118895
2
118893
3
118890
2
118888
3
118885
4
118881
1
118880
3
118877
2
118875
2
118873
1
118872
3
118869
4
118865
4
118861
2
118859
3
118856
3
118853
4
118849
2
118847
3
118844
3
118841
1
118840
2
118838
1
118837
2
118835
1
118834
3
118831
3
118828
2
118826
1
118825
4
118821
3
118818
3
118815
5
118810
5
118805
5
118800
5
118795
3
118792
5
118787
5
118782
5
118777
5
118772
2
118770
5
118765
5
118760
4
118756
5
118751
2
118749
3
118746
5
1

114448
2
114446
1
114445
4
114441
2
114439
4
114435
2
114433
3
114430
5
114425
3
114422
2
114420
2
114418
5
114413
1
114412
1
114411
1
114410
4
114406
1
114405
3
114402
4
114398
1
114397
1
114396
2
114394
2
114392
2
114390
3
114387
1
114386
3
114383
1
114382
2
114380
1
114379
2
114377
2
114375
1
114374
1
114373
3
114370
2
114368
2
114366
3
114363
1
114362
3
114359
4
114355
2
114353
1
114352
4
114348
4
114344
2
114342
2
114340
5
114335
1
114334
2
114332
3
114329
3
114326
2
114324
2
114322
1
114321
1
114320
1
114319
1
114318
9
114309
8
114301
9
114292
9
114283
9
114274
9
114265
9
114256
7
114249
9
114240
8
114232
9
114223
6
114217
8
114209
6
114203
10
114193
7
114186
6
114180
8
114172
6
114166
6
114160
10
114150
8
114142
9
114133
7
114126
9
114117
9
114108
10
114098
9
114089
7
114082
10
114072
8
114064
10
114054
8
114046
10
114036
9
114027
10
114017
10
114007
10
113997
10
113987
9
113978
10
113968
7
113961
9
113952
10
113942
10
113932
10
113922
7
113915
10
113905
10
113895
10
113885
5
11

9
108951
10
108941
10
108931
8
108923
10
108913
10
108903
10
108893
9
108884
10
108874
8
108866
10
108856
8
108848
10
108838
9
108829
6
108823
8
108815
9
108806
9
108797
10
108787
6
108781
9
108772
10
108762
7
108755
10
108745
9
108736
8
108728
8
108720
8
108712
7
108705
8
108697
9
108688
10
108678
8
108670
1
108669
4
108665
2
108663
3
108660
5
108655
3
108652
4
108648
3
108645
3
108642
3
108639
5
108634
4
108630
4
108626
3
108623
1
108622
3
108619
5
108614
2
108612
2
108610
2
108608
4
108604
1
108603
3
108600
5
108595
2
108593
3
108590
2
108588
4
108584
3
108581
3
108578
2
108576
1
108575
2
108573
3
108570
5
108565
1
108564
3
108561
4
108557
3
108554
5
108549
4
108545
4
108541
2
108539
3
108536
5
108531
4
108527
3
108524
4
108520
1
108519
4
108515
3
108512
4
108508
3
108505
4
108501
4
108497
3
108494
3
108491
9
108482
8
108474
8
108466
8
108458
4
108454
4
108450
5
108445
5
108440
5
108435
4
108431
3
108428
5
108423
3
108420
5
108415
4
108411
3
108408
4
108404
4
108400
5
108395
5
10839

...

33846
5
33841
5
33836
5
33831
5
33826
5
33821
4
33817
5
33812
5
33807
5
33802
5
33797
4
33793
5
33788
5
33783
5
33778
5
33773
5
33768
5
33763
5
33758
5
33753
8
33745
10
33735
9
33726
10
33716
10
33706
7
33699
7
33692
9
33683
10
33673
6
33667
9
33658
9
33649
10
33639
7
33632
10
33622
9
33613
8
33605
9
33596
6
33590
8
33582
8
33574
9
33565
9
33556
8
33548
9
33539
9
33530
8
33522
9
33513
9
33504
10
33494
9
33485
8
33477
10
33467
9
33458
9
33449
8
33441
9
33432
9
33423
9
33414
8
33406
10
33396
8
33388
8
33380
9
33371
9
33362
10
33352
9
33343
5
33338
5
33333
5
33328
5
33323
5
33318
5
33313
5
33308
5
33303
5
33298
5
33293
5
33288
5
33283
4
33279
5
33274
5
33269
4
33265
4
33261
5
33256
5
33251
5
33246
5
33241
5
33236
4
33232
5
33227
5
33222
4
33218
4
33214
4
33210
5
33205
4
33201
3
33198
5
33193
4
33189
5
33184
4
33180
5
33175
4
33171
4
33167
4
33163
4
33159
4
33155
5
33150
4
33146
5
33141
3
33138
5
33133
5
33128
5
33123
3
33120
4
33116
9
33107
9
33098
9
33089
9
33080
8
33072
9
33063
9
33054


26562
9
26553
9
26544
8
26536
10
26526
9
26517
10
26507
9
26498
10
26488
10
26478
15
26463
15
26448
15
26433
15
26418
9
26409
10
26399
10
26389
15
26374
15
26359
15
26344
15
26329
10
26319
9
26310
9
26301
9
26292
8
26284
9
26275
10
26265
9
26256
10
26246
10
26236
10
26226
10
26216
13
26203
15
26188
10
26178
13
26165
10
26155
10
26145
10
26135
10
26125
10
26115
10
26105
10
26095
10
26085
10
26075
10
26065
10
26055
10
26045
9
26036
10
26026
10
26016
10
26006
10
25996
10
25986
10
25976
10
25966
10
25956
10
25946
10
25936
10
25926
9
25917
10
25907
10
25897
10
25887
10
25877
10
25867
10
25857
10
25847
10
25837
10
25827
10
25817
10
25807
10
25797
11
25786
10
25776
10
25766
10
25756
10
25746
10
25736
10
25726
5
25721
5
25716
4
25712
5
25707
3
25704
4
25700
5
25695
5
25690
4
25686
4
25682
5
25677
5
25672
4
25668
5
25663
5
25658
5
25653
4
25649
4
25645
5
25640
5
25635
4
25631
5
25626
4
25622
3
25619
5
25614
5
25609
5
25604
3
25601
4
25597
5
25592
4
25588
4
25584
4
25580
4
25576
4
25572
4
25568


19715
10
19705
9
19696
8
19688
9
19679
9
19670
9
19661
9
19652
9
19643
10
19633
9
19624
8
19616
9
19607
9
19598
9
19589
10
19579
9
19570
9
19561
9
19552
10
19542
10
19532
9
19523
9
19514
20
19494
20
19474
20
19454
20
19434
19
19415
19
19396
9
19387
10
19377
10
19367
8
19359
10
19349
10
19339
10
19329
10
19319
8
19311
10
19301
8
19293
8
19285
9
19276
8
19268
9
19259
9
19250
9
19241
9
19232
8
19224
9
19215
9
19206
8
19198
9
19189
10
19179
9
19170
10
19160
9
19151
10
19141
8
19133
9
19124
7
19117
9
19108
8
19100
10
19090
8
19082
8
19074
8
19066
10
19056
15
19041
15
19026
15
19011
13
18998
15
18983
14
18969
13
18956
14
18942
15
18927
14
18913
14
18899
14
18885
12
18873
14
18859
12
18847
14
18833
11
18822
15
18807
13
18794
14
18780
15
18765
12
18753
11
18742
15
18727
15
18712
11
18701
14
18687
15
18672
15
18657
12
18645
12
18633
14
18619
14
18605
13
18592
15
18577
13
18564
15
18549
15
18534
15
18519
14
18505
5
18500
5
18495
5
18490
4
18486
4
18482
4
18478
5
18473
5
18468
5
18463
5
18458
5
1

11625
3
11622
5
11617
4
11613
4
11609
5
11604
4
11600
5
11595
4
11591
4
11587
4
11583
4
11579
5
11574
3
11571
5
11566
4
11562
5
11557
5
11552
5
11547
5
11542
5
11537
4
11533
4
11529
3
11526
4
11522
4
11518
4
11514
10
11504
10
11494
10
11484
10
11474
10
11464
10
11454
10
11444
4
11440
10
11430
8
11422
10
11412
8
11404
8
11396
10
11386
8
11378
8
11370
10
11360
8
11352
10
11342
6
11336
9
11327
9
11318
10
11308
9
11299
9
11290
8
11282
8
11274
10
11264
9
11255
10
11245
10
11235
9
11226
9
11217
10
11207
9
11198
9
11189
9
11180
8
11172
8
11164
10
11154
8
11146
8
11138
9
11129
9
11120
9
11111
9
11102
9
11093
8
11085
8
11077
10
11067
10
11057
9
11048
9
11039
10
11029
10
11019
8
11011
9
11002
9
10993
9
10984
8
10976
8
10968
9
10959
9
10950
9
10941
5
10936
3
10933
3
10930
3
10927
5
10922
3
10919
3
10916
3
10913
3
10910
4
10906
4
10902
4
10898
4
10894
4
10890
4
10886
3
10883
4
10879
3
10876
5
10871
5
10866
5
10861
4
10857
4
10853
4
10849
5
10844
4
10840
3
10837
4
10833
4
10829
5
10824
3
10821
3
10

4800
5
4795
6
4789
5
4784
5
4779
5
4774
5
4769
5
4764
5
4759
5
4754
5
4749
5
4744
5
4739
5
4734
5
4729
5
4724
5
4719
5
4714
5
4709
5
4704
5
4699
5
4694
5
4689
5
4684
5
4679
5
4674
5
4669
4
4665
3
4662
4
4658
3
4655
4
4651
3
4648
5
4643
3
4640
4
4636
5
4631
4
4627
4
4623
3
4620
4
4616
4
4612
3
4609
5
4604
5
4599
4
4595
4
4591
2
4589
5
4584
5
4579
5
4574
5
4569
4
4565
3
4562
5
4557
5
4552
4
4548
5
4543
4
4539
5
4534
4
4530
4
4526
4
4522
5
4517
4
4513
5
4508
5
4503
4
4499
3
4496
4
4492
3
4489
3
4486
4
4482
5
4477
5
4472
3
4469
5
4464
4
4460
4
4456
3
4453
4
4449
5
4444
4
4440
5
4435
3
4432
3
4429
5
4424
2
4422
5
4417
5
4412
3
4409
5
4404
5
4399
4
4395
4
4391
5
4386
4
4382
4
4378
5
4373
5
4368
10
4358
10
4348
8
4340
9
4331
9
4322
8
4314
7
4307
7
4300
9
4291
9
4282
8
4274
7
4267
8
4259
8
4251
9
4242
9
4233
8
4225
9
4216
8
4208
9
4199
9
4190
8
4182
9
4173
9
4164
9
4155
9
4146
8
4138
9
4129
9
4120
8
4112
19
4093
9
4084
10
4074
10
4064
10
4054
10
4044
10
4034
10
4024
10
4014
10
4004
10
3994
10


In [17]:
queries_pd.head()

title                        id  \
0  Beyoncé  56be85543aeaaa14008c9063   
1  Beyoncé  56be85543aeaaa14008c9065   
2  Beyoncé  56be85543aeaaa14008c9066   
3  Beyoncé  56bf6b0f3aeaaa14008c9601   
4  Beyoncé  56bf6b0f3aeaaa14008c9602   

                                               query               answer  \
0           When did Beyonce start becoming popular?    in the late 1990s   
1  What areas did Beyonce compete in when she was...  singing and dancing   
2  When did Beyonce leave Destiny's Child and bec...                 2003   
3      In what city and state did Beyonce  grow up?        Houston, Texas   
4         In which decade did Beyonce become famous?           late 1990s   

   impossible plausible dataset  \
0       False       NaN   train   
1       False       NaN   train   
2       False       NaN   train   
3       False       NaN   train   
4       False       NaN   train   

                                             context  \
0  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
1  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
2  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
3  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   
4  Beyoncé Giselle Knowles-Carter (/biːˈjɒnseɪ/ b...   

                                           query_pos  \
0  [Tag(word='When', pos='WRB', lemma='when'), Ta...   
1  [Tag(word='What', pos='WP', lemma='what'), Tag...   
2  [Tag(word='When', pos='WRB', lemma='when'), Ta...   
3  [Tag(word='In', pos='IN', lemma='in'), Tag(wor...   
4  [Tag(word='In', pos='IN', lemma='in'), Tag(wor...   

                                          answer_pos plausible_pos  \
0  [Tag(word='in', pos='IN', lemma='in'), Tag(wor...            []   
1  [Tag(word='singing', pos='NN', lemma='singing'...            []   
2       [Tag(word='2003', pos='LS', lemma='@card@')]            []   
3  [Tag(word='Houston', pos='NP', lemma='Houston'...            []   
4  [Tag(word='late', pos='JJ', lemma='late'), Tag...            []   

                                         context_pos  \
0  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...   
1  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...   
2  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...   
3  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...   
4  [Tag(word='Beyoncé', pos='NP', lemma='Beyoncé'...   

                                     query_processed  \
0            When did Beyonce start becoming popular   
1  What areas did Beyonce compete in when she was...   
2  When did Beyonce leave Destiny's Child and bec...   
3         In what city and state did Beyonce grow up   
4          In which decade did Beyonce become famous   

                                         query_ner  \
0                          {'PERSON': ['Beyonce']}   
1                          {'PERSON': ['Beyonce']}   
2     {'PERSON': ['Beyonce'], 'TITLE': ['singer']}   
3                          {'PERSON': ['Beyonce']}   
4  {'DURATION': ['decade'], 'PERSON': ['Beyonce']}   

                                        context_proc  \
0  Beyoncé Giselle Knowles Carter /biːˈjɒnseɪ/ be...   
1  Beyoncé Giselle Knowles Carter /biːˈjɒnseɪ/ be...   
2  Beyoncé Giselle Knowles Carter /biːˈjɒnseɪ/ be...   
3  Beyoncé Giselle Knowles Carter /biːˈjɒnseɪ/ be...   
4  Beyoncé Giselle Knowles Carter /biːˈjɒnseɪ/ be...   

                                         context_ner  
0  {'PERSON': ['Beyoncé Giselle Knowles Carter', ...  
1  {'PERSON': ['Beyoncé Giselle Knowles Carter', ...  
2  {'PERSON': ['Beyoncé Giselle Knowles Carter', ...  
3  {'PERSON': ['Beyoncé Giselle Knowles Carter', ...  
4  {'PERSON': ['Beyoncé Giselle Knowles Carter', ...

In [19]:
queries_pd['answer']= queries_pd['answer'].fillna('')
queries_pd['answer_processed'] = queries_pd['answer'].apply(preprocess_text)

In [20]:
queries_pd['answer_ner'] = queries_pd['answer_processed'].apply(nlp.ner)

In [21]:
queries_pd['answer_ner'] = queries_pd['answer_ner'].apply(filter_ner_relevant)

In [25]:
queries_pd.columns

Index(['title', 'id', 'query', 'answer', 'impossible', 'plausible', 'dataset',
       'context', 'query_pos', 'answer_pos', 'plausible_pos', 'context_pos',
       'query_processed', 'query_ner', 'context_proc', 'context_ner',
       'answer_processed', 'answer_ner'],
      dtype='object')

In [23]:
informe_pd = queries_pd[['title', 'id', 'query', 'answer', 'impossible', 'plausible', 'dataset',
       'context', 'query_ner', 'context_ner', 'answer_ner',
                      'query_pos',  'answer_pos','plausible_pos', 'context_pos'  ]] 

In [24]:
informe_pd.to_excel('NER-SQUAD-train-queries.xlsx', index=False)

In [113]:
#informe_pd.to_excel('NER-SQUAD-dev-queries.xlsx', index=False)